## Прогнозирование стоимости автомобиля по характеристикам - изучение данных
У нас есть собранные условной компанией записи о продаже автомобилей и данные авто.ру. На данных с сайта мы тренируем модели, на тестовых данных проверяем результат обучения. Задача - как можно точнее предсказать цену машины.
В этом ноутбуке у нас хранятся результаты исследования данных с помощью pandas_profiling.

# Загружаем нужные библиотеки

In [1]:
import requests as r
from bs4 import BeautifulSoup
import json
import time

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
from pandas import Series
import pandas_profiling

import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
pd.set_option('display.max_columns', None)

# Setup

In [3]:
VERSION    = 16
# DIR_TRAIN  = '../input/parsing-all-moscow-auto-ru-09-09-2020/' # подключил к ноутбуку внешний датасет
DIR_TEST   = '../input/sf-dst-car-price-prediction/'
VAL_SIZE   = 0.20   # 20%

# Data

In [4]:
!ls '../input'

autoru-18-07-2021	 parsing-all-moscow-auto-ru-09-09-2020
autoru-cars-dataset	 sf-dst-car-price-prediction
autoru-parsed-0603-1304


**Подключаем датасеты: тренировочный и тестовый.**

In [5]:
# train = pd.read_csv('../input/autoru-parsed-0603-1304/new_data_99_06_03_13_04.csv') # датасет для обучения модели
train = pd.read_csv('../input/autoru-cars-dataset/autoru_cars_dataset.csv')
# train = pd.read_csv('../input/autoru-18-07-2021/all_auto_ru.csv')
test = pd.read_csv(DIR_TEST+'test.csv')
sample_submission = pd.read_csv(DIR_TEST+'sample_submission.csv')

/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3063: DtypeWarning: Columns (5,9,11,14,16,19,21,22,23) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


**Первичное исследование train**

In [6]:
train.head(5)

Unnamed: 0           bodyType  brand  \
0           0  внедорожник 5 дв.  VOLVO   
1           1              седан  VOLVO   
2           3  внедорожник 5 дв.  VOLVO   
3           4              седан  VOLVO   
4           5              седан  VOLVO   

                                             car_url   color  \
0  https://auto.ru/cars/used/sale/volvo/xc90/1101...   синий   
1  https://auto.ru/cars/used/sale/volvo/s80/11013...  чёрный   
2  https://auto.ru/cars/used/sale/volvo/xc60/1100...  чёрный   
3  https://auto.ru/cars/used/sale/volvo/s60/11014...  чёрный   
4  https://auto.ru/cars/used/sale/volvo/s60/11014...   белый   

  complectation_dict                                        description  \
0        {'id': '0'}  Продажа а/м осуществляется ОФИЦИАЛЬНЫМ ДИЛЕРОМ...   
1        {'id': '0'}  При покупке автомобиля до 15 ноября  \n► Выгод...   
2        {'id': '0'}  Автодилер года 2020\n\nПобедитель в номинации ...   
3        {'id': '0'}  Объявление №690\n\nАвтомобиль в отличном состо...   
4        {'id': '0'}  Авто в отличном состоянии, вложений не требует...   

   engineDisplacement  enginePower  \
0                 2.0        235.0   
1                 2.5        249.0   
2                 2.4        190.0   
3                 2.4        170.0   
4                 1.6        150.0   

                                      equipment_dict fuelType  \
0  {'esp': True, 'airbag-driver': True, 'aux': Tr...   дизель   
1  {'cruise-control': True, 'asr': True, 'tinted-...   бензин   
2  {'cruise-control': True, 'engine-proof': True,...   дизель   
3  {'engine-proof': True, 'cruise-control': True,...   бензин   
4  {'cruise-control': True, 'asr': True, 'tinted-...   бензин   

                                               image   mileage  modelDate  \
0  //avatars.mds.yandex.net/get-autoru-vos/209286...   85452.0     2014.0   
1  //avatars.mds.yandex.net/get-autoru-vos/216441...  116410.0     2009.0   
2  //avatars.mds.yandex.net/get-autoru-vos/209157...   83657.0     2013.0   
3  //avatars.mds.yandex.net/get-autoru-vos/210185...  118000.0     2004.0   
4  //avatars.mds.yandex.net/get-autoru-vos/200015...  121421.0     2010.0   

                                          model_info model_name  \
0  {'code': 'XC90', 'name': 'XC90', 'ru_name': 'X...       XC90   
1  {'code': 'S80', 'name': 'S80', 'ru_name': 'S80...        S80   
2  {'code': 'XC60', 'name': 'XC60', 'ru_name': 'X...       XC60   
3  {'code': 'S60', 'name': 'S60', 'ru_name': 'S60...        S60   
4  {'code': 'S60', 'name': 'S60', 'ru_name': 'S60...        S60   

                     name  numberOfDoors  parsing_unixtime priceCurrency  \
0  2.0d AT (235 л.с.) 4WD            5.0      1.604647e+12           RUR   
1       2.5 AT (249 л.с.)            4.0      1.604660e+12           RUR   
2  2.4d AT (190 л.с.) 4WD            5.0      1.604656e+12           RUR   
3       2.4 AT (170 л.с.)            4.0      1.604639e+12           RUR   
4      1.6 AMT (150 л.с.)            4.0      1.604699e+12           RUR   

   productionDate              sell_id  \
0          2016.0  1101191623-464cf4be   
1          2013.0  1101345022-3e0e4f8c   
2          2016.0  1100336634-a6643416   
3          2006.0  1101497967-8c590a51   
4          2012.0  1101427740-01c03c86   

                                           super_gen  \
0  {'id': '20228874', 'name': 'II', 'ru_name': '2...   
1  {'id': '7974165', 'name': 'II Рестайлинг', 'ru...   
2  {'id': '20012324', 'name': 'I Рестайлинг', 'ru...   
3  {'id': '2309989', 'name': 'I Рестайлинг', 'ru_...   
4  {'id': '6478325', 'name': 'II', 'ru_name': '2'...   

            vehicleConfiguration vehicleTransmission    vendor    Владельцы  \
0  ALLROAD_5_DOORS AUTOMATIC 2.0      автоматическая  EUROPEAN  2 владельца   
1            SEDAN AUTOMATIC 2.5      автоматическая  EUROPEAN   1 владелец   
2  ALLROAD_5_DOORS AUTOMATIC 2.4      автоматическая  EUROPEAN   1 владелец   
3            SEDAN AUTOMATIC 2.4      автоматическая  EUROP

In [7]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 108209 entries, 0 to 108208
Data columns (total 36 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   Unnamed: 0            108209 non-null  int64  
 1   bodyType              108209 non-null  object 
 2   brand                 108209 non-null  object 
 3   car_url               108209 non-null  object 
 4   color                 108209 non-null  object 
 5   complectation_dict    20165 non-null   object 
 6   description           104798 non-null  object 
 7   engineDisplacement    108209 non-null  float64
 8   enginePower           108209 non-null  float64
 9   equipment_dict        20165 non-null   object 
 10  fuelType              108209 non-null  object 
 11  image                 20165 non-null   object 
 12  mileage               107655 non-null  float64
 13  modelDate             108209 non-null  float64
 14  model_info            20165 non-null   object 
 15  

In [8]:
# Удаляем строки с нулевой ценой
train = train.dropna(axis=0, subset=['price'])

In [9]:
train['price']

0         2799000.0
1         1277000.0
2         1869000.0
3          369000.0
4          650000.0
            ...    
108204    1605000.0
108205    1250000.0
108206    5500000.0
108207    3200000.0
108208     880000.0
Name: price, Length: 108209, dtype: float64

In [10]:
len(train) - len(train.drop_duplicates())

0

In [11]:
train = train.drop_duplicates()

In [12]:
print('Размерность тренировочного датасета: ', train.shape)
display(train.head(5))

Размерность тренировочного датасета:  (108209, 36)


Unnamed: 0           bodyType  brand  \
0           0  внедорожник 5 дв.  VOLVO   
1           1              седан  VOLVO   
2           3  внедорожник 5 дв.  VOLVO   
3           4              седан  VOLVO   
4           5              седан  VOLVO   

                                             car_url   color  \
0  https://auto.ru/cars/used/sale/volvo/xc90/1101...   синий   
1  https://auto.ru/cars/used/sale/volvo/s80/11013...  чёрный   
2  https://auto.ru/cars/used/sale/volvo/xc60/1100...  чёрный   
3  https://auto.ru/cars/used/sale/volvo/s60/11014...  чёрный   
4  https://auto.ru/cars/used/sale/volvo/s60/11014...   белый   

  complectation_dict                                        description  \
0        {'id': '0'}  Продажа а/м осуществляется ОФИЦИАЛЬНЫМ ДИЛЕРОМ...   
1        {'id': '0'}  При покупке автомобиля до 15 ноября  \n► Выгод...   
2        {'id': '0'}  Автодилер года 2020\n\nПобедитель в номинации ...   
3        {'id': '0'}  Объявление №690\n\nАвтомобиль в отличном состо...   
4        {'id': '0'}  Авто в отличном состоянии, вложений не требует...   

   engineDisplacement  enginePower  \
0                 2.0        235.0   
1                 2.5        249.0   
2                 2.4        190.0   
3                 2.4        170.0   
4                 1.6        150.0   

                                      equipment_dict fuelType  \
0  {'esp': True, 'airbag-driver': True, 'aux': Tr...   дизель   
1  {'cruise-control': True, 'asr': True, 'tinted-...   бензин   
2  {'cruise-control': True, 'engine-proof': True,...   дизель   
3  {'engine-proof': True, 'cruise-control': True,...   бензин   
4  {'cruise-control': True, 'asr': True, 'tinted-...   бензин   

                                               image   mileage  modelDate  \
0  //avatars.mds.yandex.net/get-autoru-vos/209286...   85452.0     2014.0   
1  //avatars.mds.yandex.net/get-autoru-vos/216441...  116410.0     2009.0   
2  //avatars.mds.yandex.net/get-autoru-vos/209157...   83657.0     2013.0   
3  //avatars.mds.yandex.net/get-autoru-vos/210185...  118000.0     2004.0   
4  //avatars.mds.yandex.net/get-autoru-vos/200015...  121421.0     2010.0   

                                          model_info model_name  \
0  {'code': 'XC90', 'name': 'XC90', 'ru_name': 'X...       XC90   
1  {'code': 'S80', 'name': 'S80', 'ru_name': 'S80...        S80   
2  {'code': 'XC60', 'name': 'XC60', 'ru_name': 'X...       XC60   
3  {'code': 'S60', 'name': 'S60', 'ru_name': 'S60...        S60   
4  {'code': 'S60', 'name': 'S60', 'ru_name': 'S60...        S60   

                     name  numberOfDoors  parsing_unixtime priceCurrency  \
0  2.0d AT (235 л.с.) 4WD            5.0      1.604647e+12           RUR   
1       2.5 AT (249 л.с.)            4.0      1.604660e+12           RUR   
2  2.4d AT (190 л.с.) 4WD            5.0      1.604656e+12           RUR   
3       2.4 AT (170 л.с.)            4.0      1.604639e+12           RUR   
4      1.6 AMT (150 л.с.)            4.0      1.604699e+12           RUR   

   productionDate              sell_id  \
0          2016.0  1101191623-464cf4be   
1          2013.0  1101345022-3e0e4f8c   
2          2016.0  1100336634-a6643416   
3          2006.0  1101497967-8c590a51   
4          2012.0  1101427740-01c03c86   

                                           super_gen  \
0  {'id': '20228874', 'name': 'II', 'ru_name': '2...   
1  {'id': '7974165', 'name': 'II Рестайлинг', 'ru...   
2  {'id': '20012324', 'name': 'I Рестайлинг', 'ru...   
3  {'id': '2309989', 'name': 'I Рестайлинг', 'ru_...   
4  {'id': '6478325', 'name': 'II', 'ru_name': '2'...   

            vehicleConfiguration vehicleTransmission    vendor    Владельцы  \
0  ALLROAD_5_DOORS AUTOMATIC 2.0      автоматическая  EUROPEAN  2 владельца   
1            SEDAN AUTOMATIC 2.5      автоматическая  EUROPEAN   1 владелец   
2  ALLROAD_5_DOORS AUTOMATIC 2.4      автоматическая  EUROPEAN   1 владелец   
3            SEDAN AUTOMATIC 2.4      автоматическая  EUROP

**Первичное исследование test**

In [13]:
test.head(5)

bodyType  brand                                            car_url  \
0  лифтбек  SKODA  https://auto.ru/cars/used/sale/skoda/octavia/1...   
1  лифтбек  SKODA  https://auto.ru/cars/used/sale/skoda/octavia/1...   
2  лифтбек  SKODA  https://auto.ru/cars/used/sale/skoda/superb/11...   
3  лифтбек  SKODA  https://auto.ru/cars/used/sale/skoda/octavia/1...   
4  лифтбек  SKODA  https://auto.ru/cars/used/sale/skoda/octavia/1...   

        color                                 complectation_dict  \
0       синий                                                NaN   
1      чёрный                                                NaN   
2       серый  {"id":"20026336","name":"Ambition","available_...   
3  коричневый  {"id":"20803582","name":"Ambition","available_...   
4       белый                                                NaN   

                                         description engineDisplacement  \
0  Все автомобили, представленные в продаже, прох...            1.2 LTR   
1  ЛОТ: 01217195\nАвтопрага Север\nДанный автомоб...            1.6 LTR   
2  Все автомобили, представленные в продаже, прох...            1.8 LTR   
3  КОМПЛЕКТ ЗИМНЕЙ (ЛЕТНЕЙ) РЕЗИНЫ ПО СЕЗОНУ В ПО...            1.6 LTR   
4  ЛОТ: 01220889\nАвтопрага Север\n\nВы можете по...            1.8 LTR   

  enginePower                                     equipment_dict fuelType  \
0     105 N12  {"engine-proof":true,"tinted-glass":true,"airb...   бензин   
1     110 N12  {"cruise-control":true,"asr":true,"esp":true,"...   бензин   
2     152 N12  {"cruise-control":true,"tinted-glass":true,"es...   бензин   
3     110 N12  {"cruise-control":true,"roller-blind-for-rear-...   бензин   
4     152 N12  {"cruise-control":true,"asr":true,"esp":true,"...   бензин   

                                               image  mileage  modelDate  \
0  https://autoru.naydex.net/o9DBXQ270/5ac010hAY0...    74000       2013   
1  https://autoru.naydex.net/o9DBXQ270/5ac010hAY0...    60563       2017   
2  https://avatars.mds.yandex.net/get-autoru-vos/...    88000       2013   
3  https://autoru.naydex.net/o9DBXQ270/5ac010hAY0...    95000       2013   
4  https://autoru.naydex.net/o9DBXQ270/5ac010hAY0...    58536       2008   

                                          model_info model_name  \
0  {"code":"OCTAVIA","name":"Octavia","ru_name":"...    OCTAVIA   
1  {"code":"OCTAVIA","name":"Octavia","ru_name":"...    OCTAVIA   
2  {"code":"SUPERB","name":"Superb","ru_name":"Су...     SUPERB   
3  {"code":"OCTAVIA","name":"Octavia","ru_name":"...    OCTAVIA   
4  {"code":"OCTAVIA","name":"Octavia","ru_name":"...    OCTAVIA   

                     name  numberOfDoors  parsing_unixtime priceCurrency  \
0      1.2 AMT (105 л.с.)              5        1603226273           RUB   
1       1.6 MT (110 л.с.)              5        1603226277           RUB   
2  DSG 1.8 AMT (152 л.с.)              5        1603226280           RUB   
3       1.6 AT (110 л.с.)              5        1603226284           RUB   
4       1.8 AT (152 л.с.)              5        1603226288           RUB   

   productionDate     sell_id  \
0            2014  1100575026   
1            2017  1100549428   
2            2014  1100658222   
3            2014  1100937408   
4            2012  1101037972   

                                           super_gen     vehicleConfiguration  \
0  {"id":"10373605","displacement":1197,"engine_t...       LIFTBACK ROBOT 1.2   
1  {"id":"20913311","displacement":1598,"engine_t...  LIFTBACK MECHANICAL 1.6   
2  {"id":"20026323","nameplate":"DSG","displaceme...       LIFTBACK ROBOT 1.8   
3  {"id":"20105521","displacement":1598,"engine_t...   LIFTBACK AUTOMATIC 1.6   
4  {"id":"4561004","displacement":1798,"engine_ty...   LIFTBACK AUTOMATIC 1.8   

  vehicleTransmission    vendor    Владельцы Владение       ПТС    Привод  \
0    роботизированная  EUROPEAN  3 или более      NaN  Оригинал  передний   
1        механическая  EUROPEAN   1 владелец      NaN  Оригинал  передний   
2    роботиз

In [14]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 34686 entries, 0 to 34685
Data columns (total 32 columns):
 #   Column                Non-Null Count  Dtype 
---  ------                --------------  ----- 
 0   bodyType              34686 non-null  object
 1   brand                 34686 non-null  object
 2   car_url               34686 non-null  object
 3   color                 34686 non-null  object
 4   complectation_dict    6418 non-null   object
 5   description           34686 non-null  object
 6   engineDisplacement    34686 non-null  object
 7   enginePower           34686 non-null  object
 8   equipment_dict        24690 non-null  object
 9   fuelType              34686 non-null  object
 10  image                 34686 non-null  object
 11  mileage               34686 non-null  int64 
 12  modelDate             34686 non-null  int64 
 13  model_info            34686 non-null  object
 14  model_name            34686 non-null  object
 15  name                  34686 non-null

In [15]:
# Удаляем из тестового датасета колонки, которые не удалось спарсить в тренировочный.

# test.drop(['complectation_dict', 'equipment_dict', 'model_info',
#          'super_gen', 'vendor', 'Владение'], axis=1, inplace=True)

In [16]:
# Обнуляем цену в тестовом датасете.

test['price'] = 0

In [17]:
print('Размерность тестового датасета: ', test.shape)
display(test.head(5))

Размерность тестового датасета:  (34686, 33)


bodyType  brand                                            car_url  \
0  лифтбек  SKODA  https://auto.ru/cars/used/sale/skoda/octavia/1...   
1  лифтбек  SKODA  https://auto.ru/cars/used/sale/skoda/octavia/1...   
2  лифтбек  SKODA  https://auto.ru/cars/used/sale/skoda/superb/11...   
3  лифтбек  SKODA  https://auto.ru/cars/used/sale/skoda/octavia/1...   
4  лифтбек  SKODA  https://auto.ru/cars/used/sale/skoda/octavia/1...   

        color                                 complectation_dict  \
0       синий                                                NaN   
1      чёрный                                                NaN   
2       серый  {"id":"20026336","name":"Ambition","available_...   
3  коричневый  {"id":"20803582","name":"Ambition","available_...   
4       белый                                                NaN   

                                         description engineDisplacement  \
0  Все автомобили, представленные в продаже, прох...            1.2 LTR   
1  ЛОТ: 01217195\nАвтопрага Север\nДанный автомоб...            1.6 LTR   
2  Все автомобили, представленные в продаже, прох...            1.8 LTR   
3  КОМПЛЕКТ ЗИМНЕЙ (ЛЕТНЕЙ) РЕЗИНЫ ПО СЕЗОНУ В ПО...            1.6 LTR   
4  ЛОТ: 01220889\nАвтопрага Север\n\nВы можете по...            1.8 LTR   

  enginePower                                     equipment_dict fuelType  \
0     105 N12  {"engine-proof":true,"tinted-glass":true,"airb...   бензин   
1     110 N12  {"cruise-control":true,"asr":true,"esp":true,"...   бензин   
2     152 N12  {"cruise-control":true,"tinted-glass":true,"es...   бензин   
3     110 N12  {"cruise-control":true,"roller-blind-for-rear-...   бензин   
4     152 N12  {"cruise-control":true,"asr":true,"esp":true,"...   бензин   

                                               image  mileage  modelDate  \
0  https://autoru.naydex.net/o9DBXQ270/5ac010hAY0...    74000       2013   
1  https://autoru.naydex.net/o9DBXQ270/5ac010hAY0...    60563       2017   
2  https://avatars.mds.yandex.net/get-autoru-vos/...    88000       2013   
3  https://autoru.naydex.net/o9DBXQ270/5ac010hAY0...    95000       2013   
4  https://autoru.naydex.net/o9DBXQ270/5ac010hAY0...    58536       2008   

                                          model_info model_name  \
0  {"code":"OCTAVIA","name":"Octavia","ru_name":"...    OCTAVIA   
1  {"code":"OCTAVIA","name":"Octavia","ru_name":"...    OCTAVIA   
2  {"code":"SUPERB","name":"Superb","ru_name":"Су...     SUPERB   
3  {"code":"OCTAVIA","name":"Octavia","ru_name":"...    OCTAVIA   
4  {"code":"OCTAVIA","name":"Octavia","ru_name":"...    OCTAVIA   

                     name  numberOfDoors  parsing_unixtime priceCurrency  \
0      1.2 AMT (105 л.с.)              5        1603226273           RUB   
1       1.6 MT (110 л.с.)              5        1603226277           RUB   
2  DSG 1.8 AMT (152 л.с.)              5        1603226280           RUB   
3       1.6 AT (110 л.с.)              5        1603226284           RUB   
4       1.8 AT (152 л.с.)              5        1603226288           RUB   

   productionDate     sell_id  \
0            2014  1100575026   
1            2017  1100549428   
2            2014  1100658222   
3            2014  1100937408   
4            2012  1101037972   

                                           super_gen     vehicleConfiguration  \
0  {"id":"10373605","displacement":1197,"engine_t...       LIFTBACK ROBOT 1.2   
1  {"id":"20913311","displacement":1598,"engine_t...  LIFTBACK MECHANICAL 1.6   
2  {"id":"20026323","nameplate":"DSG","displaceme...       LIFTBACK ROBOT 1.8   
3  {"id":"20105521","displacement":1598,"engine_t...   LIFTBACK AUTOMATIC 1.6   
4  {"id":"4561004","displacement":1798,"engine_ty...   LIFTBACK AUTOMATIC 1.8   

  vehicleTransmission    vendor    Владельцы Владение       ПТС    Привод  \
0    роботизированная  EUROPEAN  3 или более      NaN  Оригинал  передний   
1        механическая  EUROPEAN   1 владелец      NaN  Оригинал  передний   
2    роботиз

**Сравнение train и test**

In [18]:
#  Взяла у участников соревнования функцию по сравнению датасетов
def check_df_before_merg(d_df1,d_df2):
    
    list_of_names1 = list(d_df1.columns)
    temp_dict = {}
    temp_dict['feature_train'] = list_of_names1
    temp_dict['type_train'] = d_df1.dtypes
    temp_dict['sample_train'] = d_df1.loc[5].values
    temp_dict['# unique_train'] = d_df1.nunique().values
    temp_df1 = pd.DataFrame.from_dict(temp_dict)
    
    
    list_of_names2 = list(d_df2.columns)
    temp_dict2 = {}
    temp_dict2['feature_test'] = list_of_names2
    temp_dict2['type_test'] = d_df2.dtypes
    temp_dict2['sample_test'] = d_df2.loc[5].values
    temp_dict2['# unique_test'] = d_df2.nunique().values
    temp_df2 = pd.DataFrame.from_dict(temp_dict2)
    
    temp_insert = pd.DataFrame(columns=['< - >'])
    
    temp_df = pd.concat([temp_df1,temp_insert, temp_df2], axis=1, sort=False)
    temp_df.reset_index(inplace = True)
    del temp_df['index']
    temp_df['< - >'] = '| - |'
    display(temp_df)

    temp_dict3 = {}
    temp_df3= pd.DataFrame(temp_df)
    temp_list  = []
    temp_list2  = []
    temp_list3  = []
    temp_list4  = []
    temp_list5  = []

    for i in range(len(temp_df)):
        if str(temp_df3['type_train'][i]) != str(temp_df3['type_test'][i]):
            temp_list.append(temp_df3['feature_train'][i])
            temp_list2.append(temp_df3['feature_test'][i])
            temp_list3.append(str(temp_df3['type_train'][i]) + ' != ' + str(temp_df3['type_test'][i]))
            temp_list4.append(i)
        if temp_df3['# unique_test'][i]>0 and temp_df3['# unique_train'][i]/temp_df3['# unique_test'][i] > 2:
            temp_list5.append(i)
            
    temp_dict3['index']= temp_list4
    temp_dict3['feature_train']= temp_list
    temp_dict3['не совпадают типы'] = temp_list3
    temp_dict3['feature_test']= temp_list2

    temp_df4 = pd.DataFrame.from_dict(temp_dict3)
    temp_df4.set_index('index',inplace=True)

    print(f'Резюме:\n 1. Не совпали типы в:= {len(temp_df4)} столбцах\n')
    print(f'2. Уникальные значения различаются в:= {len(temp_list5)} столбцах {temp_list5}')
    display(temp_df4)

In [19]:
check_df_before_merg(test,train)

feature_train type_train  \
0               bodyType     object   
1                  brand     object   
2                car_url     object   
3                  color     object   
4     complectation_dict     object   
5            description     object   
6     engineDisplacement     object   
7            enginePower     object   
8         equipment_dict     object   
9               fuelType     object   
10                 image     object   
11               mileage      int64   
12             modelDate      int64   
13            model_info     object   
14            model_name     object   
15                  name     object   
16         numberOfDoors      int64   
17      parsing_unixtime      int64   
18         priceCurrency     object   
19        productionDate      int64   
20               sell_id      int64   
21             super_gen     object   
22  vehicleConfiguration     object   
23   vehicleTransmission     object   
24                vendor     object   
25             Владельцы     object   
26              Владение     object   
27                   ПТС     object   
28                Привод     object   
29                  Руль     object   
30             Состояние     object   
31               Таможня     object   
32                 price      int64   
33                   NaN        NaN   
34                   NaN        NaN   
35                   NaN        NaN   

                                         sample_train  # unique_train  < - >  \
0                                             лифтбек            24.0  | - |   
1                                               SKODA            12.0  | - |   
2   https://auto.ru/cars/used/sale/skoda/octavia_r...         34686.0  | - |   
3                                               серый            16.0  | - |   
4   {"id":"5011515","name":"RS","available_options...          2364.0  | - |   
5   Продаю свой автомобиль! Автомобиль полностью и...         31732.0  | - |   
6                                             2.0 LTR            55.0  | - |   
7                                             200 N12           315.0  | - |   
8   {"cruise-control":true,"tinted-glass":true,"es...         23705.0  | - |   
9                                              бензин             5.0  | - |   
10  https://avatars.mds.yandex.net/get-autoru-vos/...         34557.0  | - |   
11                                             172000         11268.0  | - |   
12                                               2008            66.0  | - |   
13  {"code":"OCTAVIA_RS","name":"Octavia RS","ru_n...           954.0  | - |   
14                                         OCTAVIA_RS           544.0  | - |   
15                                 2.0 AMT (200 л.с.)          2780.0  | - |   
16                                                  5             5.0  | - |   
17                                         1603226291         34686.0  | - |   
18                                                RUB             1.0  | - |   
19                                               2012            69.0  | - |   
20                                         1100912634         34686.0  | - |   
21  {"id":"5009158","displacement":1984,"engine_ty...          5890.0  | - |   
22                                 LIFTBACK ROBOT 2.0           634.0  | - |   
23                                   роботизированная             4.0  | - |   
24                                           EUROPEAN             2.0  | - |   
25                                        3 или более             3.0  | - |   
26                                                NaN           275.0  | - |   
27                                           Оригинал             2.0  | - |   
28                                           передний             3.0  | - |   
29                                              Левый             2.0  | - |   
30                                 Не требует ремонта             1.0  | - |   
31     

Резюме:
 1. Не совпали типы в:= 12 столбцах

2. Уникальные значения различаются в:= 3 столбцах [13, 15, 21]


feature_train  не совпадают типы        feature_test
index                                                           
6      engineDisplacement  object != float64  engineDisplacement
7             enginePower  object != float64         enginePower
11                mileage   int64 != float64             mileage
12              modelDate   int64 != float64           modelDate
16          numberOfDoors   int64 != float64       numberOfDoors
17       parsing_unixtime   int64 != float64    parsing_unixtime
19         productionDate   int64 != float64      productionDate
20                sell_id    int64 != object             sell_id
32                  price   int64 != float64               price
33                    NaN       nan != int64          Unnamed: 0
34                    NaN     nan != float64        acceleration
35                    NaN     nan != float64           fuel_rate

In [20]:
# Создадим список переменных для теста и трейна:
cols = ['sell_id', 'bodyType', 'brand', 'color', 'fuelType', 'modelDate',
           'name', 'model_name', 'numberOfDoors', 'productionDate', 
           'vehicleConfiguration', 'vehicleTransmission', 'engineDisplacement',
           'enginePower', 'description', 'mileage', 'Привод',
           'Руль', 'Владельцы', 'ПТС', 'Таможня','Владение', 
           'Состояние','price', 'train']

# Объединение датасета

In [21]:
# Объединяем тренировочные и тестовые данные в один датасет.
train['train'] = 1 # помечаем тренировочные
test['train'] = 0 # помечаем тестовые
cars = pd.concat([train, test], ignore_index=True) # оставляем датасет для последующего сравнений и делаем копию для манипуляций
df = cars.copy()
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 142895 entries, 0 to 142894
Data columns (total 37 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   Unnamed: 0            108209 non-null  float64
 1   bodyType              142895 non-null  object 
 2   brand                 142895 non-null  object 
 3   car_url               142895 non-null  object 
 4   color                 142895 non-null  object 
 5   complectation_dict    26583 non-null   object 
 6   description           139484 non-null  object 
 7   engineDisplacement    142895 non-null  object 
 8   enginePower           142895 non-null  object 
 9   equipment_dict        44855 non-null   object 
 10  fuelType              142895 non-null  object 
 11  image                 54851 non-null   object 
 12  mileage               142341 non-null  float64
 13  modelDate             142895 non-null  float64
 14  model_info            54851 non-null   object 
 15  

In [22]:
df.head()

Unnamed: 0           bodyType  brand  \
0         0.0  внедорожник 5 дв.  VOLVO   
1         1.0              седан  VOLVO   
2         3.0  внедорожник 5 дв.  VOLVO   
3         4.0              седан  VOLVO   
4         5.0              седан  VOLVO   

                                             car_url   color  \
0  https://auto.ru/cars/used/sale/volvo/xc90/1101...   синий   
1  https://auto.ru/cars/used/sale/volvo/s80/11013...  чёрный   
2  https://auto.ru/cars/used/sale/volvo/xc60/1100...  чёрный   
3  https://auto.ru/cars/used/sale/volvo/s60/11014...  чёрный   
4  https://auto.ru/cars/used/sale/volvo/s60/11014...   белый   

  complectation_dict                                        description  \
0        {'id': '0'}  Продажа а/м осуществляется ОФИЦИАЛЬНЫМ ДИЛЕРОМ...   
1        {'id': '0'}  При покупке автомобиля до 15 ноября  \n► Выгод...   
2        {'id': '0'}  Автодилер года 2020\n\nПобедитель в номинации ...   
3        {'id': '0'}  Объявление №690\n\nАвтомобиль в отличном состо...   
4        {'id': '0'}  Авто в отличном состоянии, вложений не требует...   

  engineDisplacement enginePower  \
0                  2         235   
1                2.5         249   
2                2.4         190   
3                2.4         170   
4                1.6         150   

                                      equipment_dict fuelType  \
0  {'esp': True, 'airbag-driver': True, 'aux': Tr...   дизель   
1  {'cruise-control': True, 'asr': True, 'tinted-...   бензин   
2  {'cruise-control': True, 'engine-proof': True,...   дизель   
3  {'engine-proof': True, 'cruise-control': True,...   бензин   
4  {'cruise-control': True, 'asr': True, 'tinted-...   бензин   

                                               image   mileage  modelDate  \
0  //avatars.mds.yandex.net/get-autoru-vos/209286...   85452.0     2014.0   
1  //avatars.mds.yandex.net/get-autoru-vos/216441...  116410.0     2009.0   
2  //avatars.mds.yandex.net/get-autoru-vos/209157...   83657.0     2013.0   
3  //avatars.mds.yandex.net/get-autoru-vos/210185...  118000.0     2004.0   
4  //avatars.mds.yandex.net/get-autoru-vos/200015...  121421.0     2010.0   

                                          model_info model_name  \
0  {'code': 'XC90', 'name': 'XC90', 'ru_name': 'X...       XC90   
1  {'code': 'S80', 'name': 'S80', 'ru_name': 'S80...        S80   
2  {'code': 'XC60', 'name': 'XC60', 'ru_name': 'X...       XC60   
3  {'code': 'S60', 'name': 'S60', 'ru_name': 'S60...        S60   
4  {'code': 'S60', 'name': 'S60', 'ru_name': 'S60...        S60   

                     name  numberOfDoors  parsing_unixtime priceCurrency  \
0  2.0d AT (235 л.с.) 4WD            5.0      1.604647e+12           RUR   
1       2.5 AT (249 л.с.)            4.0      1.604660e+12           RUR   
2  2.4d AT (190 л.с.) 4WD            5.0      1.604656e+12           RUR   
3       2.4 AT (170 л.с.)            4.0      1.604639e+12           RUR   
4      1.6 AMT (150 л.с.)            4.0      1.604699e+12           RUR   

   productionDate              sell_id  \
0          2016.0  1101191623-464cf4be   
1          2013.0  1101345022-3e0e4f8c   
2          2016.0  1100336634-a6643416   
3          2006.0  1101497967-8c590a51   
4          2012.0  1101427740-01c03c86   

                                           super_gen  \
0  {'id': '20228874', 'name': 'II', 'ru_name': '2...   
1  {'id': '7974165', 'name': 'II Рестайлинг', 'ru...   
2  {'id': '20012324', 'name': 'I Рестайлинг', 'ru...   
3  {'id': '2309989', 'name': 'I Рестайлинг', 'ru_...   
4  {'id': '6478325', 'name': 'II', 'ru_name': '2'...   

            vehicleConfiguration vehicleTransmission    vendor    Владельцы  \
0  ALLROAD_5_DOORS AUTOMATIC 2.0      автоматическая  EUROPEAN  2 владельца   
1            SEDAN AUTOMATIC 2.5      автоматическая  EUROPEAN   1 владелец   
2  ALLROAD_5_DOORS AUTOMATIC 2.4      автоматическая  EUROPEAN   1 владелец   
3            SEDAN AUTOMATIC 2.4      автоматическая  EUROPEAN  3 или б

In [23]:
df = df[cols]

In [24]:
# Приведем колонки к более аккуратным названиям:

df.rename(columns={'bodyType': 'body_type', 
                     'engineDisplacement': 'engine_volume',
                     'enginePower': 'engine_power',
                     'fuelType': 'fuel_type',
                     'modelDate': 'model_date',
                     'numberOfDoors': 'doors',
                     'productionDate': 'production_date',
                     'vehicleConfiguration': 'vehicle_configuration',
                     'vehicleTransmission': 'transmission',
                     'Владельцы': 'owners_qty',
                     'Владение': 'ownership_time',
                     'ПТС': 'licence',
                     'Привод': 'type_of_drive',
                     'Руль': 'steering_wheel',
                     'Таможня': 'customs', 
                     'Состояние': 'state',
                     'Price': 'price'}, inplace=True)

In [25]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 142895 entries, 0 to 142894
Data columns (total 25 columns):
 #   Column                 Non-Null Count   Dtype  
---  ------                 --------------   -----  
 0   sell_id                54851 non-null   object 
 1   body_type              142895 non-null  object 
 2   brand                  142895 non-null  object 
 3   color                  142895 non-null  object 
 4   fuel_type              142895 non-null  object 
 5   model_date             142895 non-null  float64
 6   name                   54851 non-null   object 
 7   model_name             142895 non-null  object 
 8   doors                  142895 non-null  float64
 9   production_date        142895 non-null  float64
 10  vehicle_configuration  54851 non-null   object 
 11  transmission           142895 non-null  object 
 12  engine_volume          142895 non-null  object 
 13  engine_power           142895 non-null  object 
 14  description            139484 non-nu

In [26]:
# делаем быстрый EDA с помощью pandas_profiling.
pandas_profiling.ProfileReport(df)